In [ ]:
import cv2
import numpy as np
import time
import onnxruntime as ort
from ultralytics import YOLO
from PIL import Image
from torchvision import transforms
import json
import os
import threading
from flask import Flask, Response, jsonify
from flask_cors import CORS

# Global variables for video streaming
app = Flask(__name__)
CORS(app)  # Enable CORS for all routes
output_frame = None
lock = threading.Lock()

class EmotionDetectionSystem:
    def __init__(self, yolo_model_path, vit_onnx_path, emotion_labels):
        """
        Initialize the system with YOLO and ViT ONNX models
        """
        # Load YOLOv10 model
        self.yolo_model = YOLO(yolo_model_path)
        
        # Load ONNX model
        self.ort_session = ort.InferenceSession(vit_onnx_path, providers=["CUDAExecutionProvider", "CPUExecutionProvider"])
        self.input_name = self.ort_session.get_inputs()[0].name
        
        # Emotion labels
        self.emotion_labels = emotion_labels

        # Define image transformations for ONNX input (same as ViT expected format)
        self.transform = transforms.Compose([
            transforms.Resize((224, 224)),
            transforms.ToTensor(),
            transforms.Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225])
        ])
        
        self.frame_count = 0
        self.start_time = time.time()
        self.fps = 0
        
        # Define the JSON file path
        self.json_file_path = os.path.join(os.path.expanduser("~"), "RASA BOTSS", "draft2", "shared_emotion_data.json")
        print(f"JSON file will be saved at: {self.json_file_path}")
        
        # Make sure directory exists
        os.makedirs(os.path.dirname(self.json_file_path), exist_ok=True)
        
        # Initialize with neutral emotion
        self.update_emotion_state("neutral", 1.0)
    
    def update_emotion_state(self, emotion, confidence):
        """Write current emotion to a file that RASA can access"""
        try:
            # Create data structure
            emotion_data = {
                "timestamp": time.time(),
                "emotion": emotion,
                "confidence": float(confidence), 
                "last_updated": time.strftime("%Y-%m-%d %H:%M:%S")
            }
            
            # Save to file
            with open(self.json_file_path, "w") as f:
                json.dump(emotion_data, f)
        except Exception as e:
            print(f"Error updating emotion state: {e}")
    
    def update_detection_status(self, status="no_face_detected"):
        """Update status when no face is detected"""
        try:
            # Create data structure for no detection
            status_data = {
                "timestamp": time.time(),
                "detection_status": status,
                "last_updated": time.strftime("%Y-%m-%d %H:%M:%S")
            }
            
            # Save to file
            with open(self.json_file_path, "w") as f:
                json.dump(status_data, f)
        except Exception as e:
            print(f"Error updating detection status: {e}")
    
    def preprocess_face(self, face_img):
        """
        Preprocess face image for ONNX model
        """
        pil_img = Image.fromarray(cv2.cvtColor(face_img, cv2.COLOR_BGR2RGB))
        img_tensor = self.transform(pil_img).unsqueeze(0).numpy().astype(np.float32)
        return img_tensor
    
    def predict_emotion(self, face_tensor):
        """
        Predict emotion using ONNX ViT model
        """
        outputs = self.ort_session.run(None, {self.input_name: face_tensor})
        logits = outputs[0]
        probabilities = np.exp(logits) / np.sum(np.exp(logits), axis=1, keepdims=True)
        pred_idx = np.argmax(probabilities)
        emotion = self.emotion_labels[pred_idx]
        confidence = probabilities[0][pred_idx]
        return emotion, confidence
    
    def process_frame(self, frame):
        """
        Process a frame to detect faces and emotions
        """
        global output_frame
        
        results = self.yolo_model(frame)
        detections = results[0].boxes
        
        self.frame_count += 1
        elapsed_time = time.time() - self.start_time
        if elapsed_time > 1.0:
            self.fps = self.frame_count / elapsed_time
            self.frame_count = 0
            self.start_time = time.time()
        
        cv2.putText(frame, f"FPS: {self.fps:.1f}", (10, 30), 
                    cv2.FONT_HERSHEY_SIMPLEX, 1, (0, 255, 0), 2)
        
        best_face = None
        best_face_area = 0
        
        # Find the largest face in the frame
        for det in detections:
            x1, y1, x2, y2 = map(int, det.xyxy[0])
            face_img = frame[y1:y2, x1:x2]
            face_area = (x2 - x1) * (y2 - y1)
            
            if face_img.size == 0 or face_img.shape[0] < 20 or face_img.shape[1] < 20:
                continue
                
            if face_area > best_face_area:
                best_face = (x1, y1, x2, y2, face_img)
                best_face_area = face_area
        
        # Process the largest face (if any were found)
        if best_face:
            x1, y1, x2, y2, face_img = best_face
            try:
                face_tensor = self.preprocess_face(face_img)
                emotion, confidence = self.predict_emotion(face_tensor)
                
                # Draw bounding box
                cv2.rectangle(frame, (x1, y1), (x2, y2), (255, 255, 255), 2)
                
                # Add emotion label below the face
                label = f"{emotion} ({confidence*100:.1f}%)"
                (w, h), _ = cv2.getTextSize(label, cv2.FONT_HERSHEY_SIMPLEX, 0.6, 2)
                text_x = x1 + (x2 - x1 - w) // 2
                
                # Draw a background for the text to make it more readable
                cv2.rectangle(frame, 
                             (text_x - 5, y1 - h - 15), 
                             (text_x + w + 5, y1 - 5), 
                             (0, 0, 0), 
                             -1)
                             
                # Draw the text for the emotion label
                cv2.putText(frame, label, (text_x, y1 - 10),
                            cv2.FONT_HERSHEY_SIMPLEX, 0.6, (255, 255, 255), 2)
                
                # Update the emotion state JSON
                self.update_emotion_state(emotion, confidence)
                
            except Exception as e:
                print(f"Error processing face: {e}")
        else:
            # No face detected, update status
            self.update_detection_status()
        
        # Update the output frame for streaming
        with lock:
            output_frame = frame.copy()
        
        return frame
    
    def run_webcam(self, camera_id=0):
        """
        Process webcam feed and perform emotion detection
        """
        cap = cv2.VideoCapture(camera_id)
        if not cap.isOpened():
            print("Error: Could not open webcam")
            return
        
        print("Press 'q' to quit")
        while cap.isOpened():
            ret, frame = cap.read()
            if not ret:
                break
                
            processed_frame = self.process_frame(frame)
            
            # Display the processed frame locally (optional)
            cv2.imshow('Emotion Detection', processed_frame)
            
            if cv2.waitKey(1) & 0xFF == ord('q'):
                break
                
        cap.release()
        cv2.destroyAllWindows()

# API routes for accessing emotion data and controlling the detection process
@app.route('/api/emotion-data')
def get_emotion_data():
    """API endpoint to get the current emotion data"""
    try:
        json_file_path = os.path.join(os.path.expanduser("~"), "RASA BOTSS", "draft2", "shared_emotion_data.json")
        
        if not os.path.exists(json_file_path):
            return jsonify({
                "timestamp": time.time(),
                "detection_status": "initializing",
                "last_updated": time.strftime("%Y-%m-%d %H:%M:%S")
            })
        
        with open(json_file_path, 'r') as f:
            data = json.load(f)
        
        return jsonify(data)
    except Exception as e:
        print(f"Error reading emotion data: {e}")
        return jsonify({
            "timestamp": time.time(),
            "detection_status": "error",
            "last_updated": time.strftime("%Y-%m-%d %H:%M:%S")
        })

@app.route('/video_feed')
def video_feed():
    """Route for streaming video feed with emotion detection"""
    return Response(generate_frames(),
                    mimetype='multipart/x-mixed-replace; boundary=frame')
@app.route('/')
def index():
    """Root route with better error handling"""
    try:
        return "Emotion Detection API is running. Use /video_feed to see the stream."
    except Exception as e:
        print(f"Error in root route: {e}")
        return f"API is initializing. Please try again in a moment. Error: {str(e)}", 503  # S

def generate_frames():
    """Generator function for video streaming"""
    global output_frame
    while True:
        with lock:
            if output_frame is None:
                continue
                
            # Encode the frame as JPEG
            (flag, encoded_image) = cv2.imencode(".jpg", output_frame)
            if not flag:
                continue
                
        # Yield the frame in the response
        yield(b'--frame\r\n' b'Content-Type: image/jpeg\r\n\r\n' + 
              bytearray(encoded_image) + b'\r\n')
# Add a global variable to track server readiness
server_ready = False

# Modified run_flask function
def run_flask():
    """Run Flask server in a separate thread"""
    # Wait for the emotion detection system to initialize
    while not server_ready:
        time.sleep(0.1)
    
    app.run(host='0.0.0.0', port=5000, threaded=True)

if __name__ == "__main__":
    # Path to your models
    yolo_model_path = r"C:\Users\hari\runs\detect\train\weights\best.pt"
    vit_onnx_path = "model_v2.onnx"
    emotion_labels = ["angry", "disgust", "fear", "happy", "neutral", "sad", "surprised"]

    # Create the emotion detection system
    emotion_system = EmotionDetectionSystem(
        yolo_model_path=yolo_model_path,
        vit_onnx_path=vit_onnx_path,
        emotion_labels=emotion_labels
    )
    
    # Set the server as ready before starting Flask
    server_ready = True
    
    # Start Flask server in a separate thread
    flask_thread = threading.Thread(target=run_flask, daemon=True)
    flask_thread.start()
    
    # Run the webcam processing
    emotion_system.run_webcam()

JSON file will be saved at: C:\Users\hari\RASA BOTSS\draft2\shared_emotion_data.json
 * Serving Flask app '__main__'
 * Debug mode: off


C:\Users\hari\anaconda3\Lib\site-packages\onnxruntime\capi\onnxruntime_inference_collection.py:118: UserWarning: Specified provider 'CUDAExecutionProvider' is not in available provider names.Available providers: 'AzureExecutionProvider, CPUExecutionProvider'
  warnings.warn(
 * Running on all addresses (0.0.0.0)
 * Running on http://127.0.0.1:5000
 * Running on http://127.0.0.1:5000
Press CTRL+C to quit


Press 'q' to quit

0: 480x640 1 face, 127.7ms
Speed: 5.0ms preprocess, 127.7ms inference, 2.6ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 1 face, 62.7ms
Speed: 2.3ms preprocess, 62.7ms inference, 0.3ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 1 face, 71.6ms
Speed: 2.0ms preprocess, 71.6ms inference, 0.3ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 1 face, 63.9ms
Speed: 2.1ms preprocess, 63.9ms inference, 0.3ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 1 face, 69.1ms
Speed: 1.7ms preprocess, 69.1ms inference, 0.3ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 1 face, 69.2ms
Speed: 2.2ms preprocess, 69.2ms inference, 0.3ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 1 face, 67.4ms
Speed: 2.5ms preprocess, 67.4ms inference, 0.3ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 1 face, 64.2ms
Speed: 2.0ms preprocess, 64.2ms inference, 0.2ms postprocess per image at shape (1, 3

127.0.0.1 - - [29/Apr/2025 10:31:58] "GET /api/emotion-data HTTP/1.1" 200 -



0: 480x640 (no detections), 238.3ms
Speed: 4.3ms preprocess, 238.3ms inference, 0.5ms postprocess per image at shape (1, 3, 480, 640)



...


0: 480x640 1 face, 71.4ms
Speed: 2.4ms preprocess, 71.4ms inference, 0.7ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 1 face, 80.7ms
Speed: 2.5ms preprocess, 80.7ms inference, 0.5ms postprocess per image at shape (1, 3, 480, 640)


127.0.0.1 - - [29/Apr/2025 12:03:13] "GET /api/emotion-data HTTP/1.1" 200 -



0: 480x640 1 face, 83.5ms
Speed: 1.7ms preprocess, 83.5ms inference, 0.7ms postprocess per image at shape (1, 3, 480, 640)

0: 480x640 2 faces, 76.4ms
Speed: 1.8ms preprocess, 76.4ms inference, 0.4ms postprocess per image at shape (1, 3, 480, 640)


127.0.0.1 - - [29/Apr/2025 12:03:13] "GET /api/emotion-data HTTP/1.1" 200 -



0: 480x640 1 face, 76.5ms
Speed: 1.8ms preprocess, 76.5ms inference, 0.4ms postprocess per image at shape (1, 3, 480, 640)



In [4]:
http://192.168.1.102:5000/api/emotion-data


SyntaxError: invalid syntax (26003004.py, line 1)

127.0.0.1 - - [15/Apr/2025 14:46:20] "GET /api/emotion-data HTTP/1.1" 200 -
127.0.0.1 - - [15/Apr/2025 14:46:21] "GET /api/emotion-data HTTP/1.1" 200 -
127.0.0.1 - - [15/Apr/2025 14:46:22] "GET /api/emotion-data HTTP/1.1" 200 -
127.0.0.1 - - [15/Apr/2025 14:46:23] "GET /api/emotion-data HTTP/1.1" 200 -
127.0.0.1 - - [15/Apr/2025 14:46:24] "GET /api/emotion-data HTTP/1.1" 200 -
127.0.0.1 - - [15/Apr/2025 14:46:25] "GET /api/emotion-data HTTP/1.1" 200 -
127.0.0.1 - - [15/Apr/2025 14:46:26] "GET /api/emotion-data HTTP/1.1" 200 -
127.0.0.1 - - [15/Apr/2025 14:46:27] "GET /api/emotion-data HTTP/1.1" 200 -
127.0.0.1 - - [15/Apr/2025 14:46:28] "GET /api/emotion-data HTTP/1.1" 200 -
127.0.0.1 - - [15/Apr/2025 14:46:29] "GET /api/emotion-data HTTP/1.1" 200 -
127.0.0.1 - - [15/Apr/2025 14:46:30] "GET /api/emotion-data HTTP/1.1" 200 -
